In [1]:
# Tensorflow / Keras
from tensorflow import keras # for building Neural Networks
from keras.models import Sequential # for creating a linear stack of layers for our Neural Network
from keras import Input # for instantiating a keras tensor
from keras.layers import Dense # for creating regular densely-connected NN layers.
import tensorflow as tf
from tensorflow.keras.callbacks import EarlyStopping

# Data manipulation
import pandas as pd # for data manipulation
import numpy as np # for data manipulation

# Sklearn
import sklearn # for model evaluation
from sklearn.model_selection import train_test_split # for splitting data into train and test samples
from sklearn.metrics import confusion_matrix, accuracy_score, precision_score, recall_score, f1_score, roc_auc_score

# Erstellung eigener Aktivierungsfunktion
from keras import backend as K
import os
import scipy
from sklearn.mixture import GaussianMixture

# Tensorflow / Keras
from tensorflow import keras # for building Neural Networks
from keras.models import Sequential, load_model # add load_model to the import

In [5]:
class gmm_model():

    def __init__(self):
        self.test_size = 0.35
        self.p = 0.3

    def import_data(self, sample_size = 11500):
        csv_files = []
        for filename in os.listdir():
            if filename == "Datasets":
                for csv_file in os.listdir(filename):
                    if csv_file.endswith('.csv'):
                        csv_files.append(csv_file)
        raw_data = pd.read_csv(os.path.join("Datasets", csv_files[2]))
        
        # Auswahl von 4000 zufälligen Zeilen
        raw_data = raw_data.sample(n=sample_size, random_state=42)
        
        Y = raw_data["label"]
        X = raw_data.drop(["label"], axis=1)

        return X, Y, raw_data

    def gen_gmm(self, data):
        data.drop(["label"], axis=1, inplace=True)
        # erstellen GMM über gesamtes
        gmm = GaussianMixture(n_components=3, covariance_type="diag")
        gmm.fit(data)
        
        return gmm

    def gen_miss_values(self, data, p):
        shape = data.shape
        new_df = data.copy().astype(np.float64)
        missing = np.random.binomial(1, self.p, shape)
        data[missing.astype('bool')] = np.nan

        return data

    def train_test_split(self, X, Y, test_size):
        # train_test_split
        X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=self.test_size, random_state=42)
        return X_train, X_test, y_train, y_test

    def gmm_activation_smieja(self, data_missing, gmm, model):
        w = model.layers[0].get_weights()[0]  # Gewichte von erster Schicht
        b = model.layers[0].get_weights()[1][:, np.newaxis]  # Bias erste Schicht
        output_list = []
        # man muss nur durch spalten iterieren
        for s in range(0, len(pd.DataFrame(w).columns)):
            for i in range(0, len(data_missing)):  # iteriere DF mit NaN-Values
                list_nan = np.array(data_missing.iloc[i])

                result = 0
                for ii in range(0, gmm.n_components):  # iteriere GMM mit n_komp
                    list_gmm_cov = gmm.covariances_[ii]
                    list_gmm_mean = gmm.means_[ii]
                    p_i = gmm.weights_[ii]

                    # Erstellen von GMM-Vektoren
                    # create cov_gmm: in gmm_covariances_vektor werte 0 setzen die in der jeweiligen Spalte von data_missing nicht NaN sind
                    global s_i
                    s_i = []
                    for y in range(len(list_gmm_cov)):
                        if np.isnan(list_nan[y]):
                            s_i.append(list_gmm_cov[y])
                        else:
                            s_i.append(0)

                    # create mean_gmm: in gmm_mean_vektor werden alle festen werte aufgenommen aus data_missing und NaN-Werte durch list_gmm_mean ersetzt
                    m_i = []
                    for y in range(len(list_gmm_mean)):
                        if not np.isnan(list_nan[y]):
                            m_i.append(list_nan[y])
                        else:
                            m_i.append(list_gmm_mean[y])

                    # Berechnen ReLUw,b(F)
                    ft = p_i * np.sqrt(np.transpose(np.array(w[:, s]) * w[:, s]) @ s_i)
                    z = np.transpose(np.array(w[:, s])) @ m_i + b[s]  # Zähler für NR w
                    n = np.sqrt(np.transpose(np.array(w[:, s]) * w[:, s]) @ s_i)  # Nenner für NR w
                    nr_w = z / n  # Input in NR
                    nr = 1 / np.sqrt(2 * np.pi) * np.exp(-(np.square(nr_w) / 2)) + (nr_w / 2) * (
                                1 + scipy.special.erf(nr_w / np.sqrt(2)))  # NR-Funktion
                    ReLUwb = ft * nr  # Summe aus i-GMM-Komponenten
                    # print(f'ReLUwb:{ReLUwb:} ft:{ft:} z:{z:} n:{n:} nr_w:{nr_w:} nr:{nr:}')
                    result += ReLUwb
                    # print(f'resutl{result}')
            output_list.append(result)
        return output_list

    def model_01(self, X_train, X_test, y_train, y_test):
        model = tf.keras.Sequential(name="Model")
        model.add(tf.keras.layers.Dense(units=32, activation=tf.nn.relu, input_shape=[len(X_train.columns)]))
        model.add(tf.keras.layers.Dense(units=64, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=128, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=10, activation=tf.nn.softmax))
        model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
        early_stop = EarlyStopping(monitor='val_loss', patience=5)

        # Fit model with early stopping
        model.fit(X_train, tf.keras.utils.to_categorical(y_train), epochs=50,
                  validation_data=(X_test, tf.keras.utils.to_categorical(y_test)),
                  callbacks=[early_stop])
        return model

    def model_02(self, X_train, X_test, y_train, y_test):
        model = tf.keras.Sequential(name="Model")
        model.add(tf.keras.layers.Dense(units=32, activation=tf.nn.relu, input_shape=[len(X_train.columns)]))
        model.add(tf.keras.layers.Dense(units=64, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=128, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=256, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=10, activation=tf.nn.softmax))
        model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
        early_stop = EarlyStopping(monitor='val_loss', patience=5)

        # Fit model with early stopping
        model.fit(X_train, tf.keras.utils.to_categorical(y_train), epochs=50,
                  validation_data=(X_test, tf.keras.utils.to_categorical(y_test)),
                  callbacks=[early_stop])
        return model

    def model_03(self, X_train, X_test, y_train, y_test):
        model = tf.keras.Sequential(name="Model")
        model.add(tf.keras.layers.Dense(units=100, activation=tf.nn.relu, input_shape=[len(X_train.columns)]))
        model.add(tf.keras.layers.Dense(units=400, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=600, activation=tf.nn.relu))
        model.add(tf.keras.layers.Dense(units=10, activation=tf.nn.softmax))
        model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
        early_stop = EarlyStopping(monitor='val_loss', patience=5)

        # Fit model with early stopping
        model.fit(X_train, tf.keras.utils.to_categorical(y_train), epochs=50,
                  validation_data=(X_test, tf.keras.utils.to_categorical(y_test)),
                  callbacks=[early_stop])
        return model

    def predict_model(self, X_test_m, model):
        if len(model.layers) == 4:
            predictions = []
            for index, row in X_test_m.iterrows():
                row_df = pd.DataFrame([row])
                row_df.columns = [f"x{i + 1}" for i in range(len(row_df.columns))]

                gmm_output = self.gmm_activation_smieja(row_df, gmm, model)

                input_data = np.array(gmm_output).reshape((1, len(gmm_output)))
                get_layer_output = K.function([model.layers[1].input], [model.layers[1].output])
                output = get_layer_output([input_data])[0]
                get_layer_output = K.function([model.layers[2].input], [model.layers[2].output])
                output = get_layer_output([output])[0]
                get_layer_output = K.function([model.layers[3].input], [model.layers[3].output])
                output = get_layer_output([output])[0]
                index_of_max = np.argmax(output)
                print(f'output:{output} index_of_max:{index_of_max}')
                predictions.append(index_of_max)

            return predictions

        elif len(model.layers) == 5:
            predictions = []
            for index, row in X_test_m.iterrows():
                row_df = pd.DataFrame([row])
                row_df.columns = [f"x{i + 1}" for i in range(len(row_df.columns))]

                gmm_output = self.gmm_activation_smieja(row_df, gmm, model)

                input_data = np.array(gmm_output).reshape((1, len(gmm_output)))
                get_layer_output = K.function([model.layers[1].input], [model.layers[1].output])
                output = get_layer_output([input_data])[0]
                get_layer_output = K.function([model.layers[2].input], [model.layers[2].output])
                output = get_layer_output([output])[0]
                get_layer_output = K.function([model.layers[3].input], [model.layers[3].output])
                output = get_layer_output([output])[0]
                get_layer_output = K.function([model.layers[4].input], [model.layers[4].output])
                output = get_layer_output([output])[0]
                index_of_max = np.argmax(output)
                print(f'output:{output} index_of_max:{index_of_max}')
                predictions.append(index_of_max)

            return predictions

        else:
            print("Something wrong")

    def evaluate(self, y_test, y_gmm_nan):
        y_true = y_test
        y_pred = y_gmm_nan
        conf_matrix = confusion_matrix(y_true, y_pred)

        # Compute the accuracy
        accuracy = accuracy_score(y_true, y_pred)

        # Compute the precision
        precision_scores = precision_score(y_true, y_pred, labels=range(len(conf_matrix)), average=None)

        # Compute the recall
        recall = recall_score(y_true, y_pred, labels=range(len(conf_matrix)), average=None)

        # Compute the F1-score
        f1 = f1_score(y_true, y_pred, labels=range(len(conf_matrix)), average=None)

        # Compute the average accuracy
        avg_accuracy = sum(precision_scores) / 5

        # Compute the predicted probabilities
        y_scores = np.random.rand(len(y_true), len(np.unique(y_true)))

        # Compute the AUC for each class
        n_classes = conf_matrix.shape[0]
        auc_list = []
        for i in range(n_classes):
            auc_list.append(roc_auc_score(y_true == i, y_scores[:, i]))

        # Define the result dictionary
        result = {
            "confusion_matrix": conf_matrix,
            "accuracy": accuracy,
            "precision": precision_scores,
            "recall": recall,
            "f1_score": f1,
            "avg_accuracy": avg_accuracy,
            "auc": auc_list
        }
        return result

    def save_txt(self, filename, evaluate):
        with open(filename, 'w') as f:
            f.write(str(evaluate))


# Model_01-_03 Test
# p = 0.3,  0.6, 0,9

# List of models to test
models = [("Model_01", "predictions_D2_01_"), ("Model_02", "predictions_D2_02_"), ("Model_03", "predictions_D2_03_")]

# List of missing values percentages to test
p_values = [0.3, 0.6, 0.9]

for model_name, output_prefix in models:
    # Initialize model and prepare data
    model = gmm_model()
    X_raw, Y_raw, data_raw = model.import_data()
    X_train, X_test, y_train, y_test = model.train_test_split(X_raw, Y_raw, 0.33)

    # Load model and create gmm
    if model_name == "Model_01":
        trained_model = load_model('model_D2_01.h5')  # load the model instead of creating it
    elif model_name == "Model_02":
        trained_model = load_model('model_D2_02.h5')  # load the model instead of creating it
    elif model_name == "Model_03":
        trained_model = load_model('model_D2_03.h5')  # load the model instead of creating it
    gmm = model.gen_gmm(data_raw)

    for p in p_values:
        # Generate missing values data and predict values
        data_miss = model.gen_miss_values(X_test, p)
        predictions = model.predict_model(data_miss, trained_model)

        # Evaluate model and save results to file
        evaluate = model.evaluate(y_test, predictions)
        output_filename = output_prefix + str(p).replace(".", "_")
        model.save_txt(output_filename, evaluate)

output:[[3.4679834e-02 2.7409740e-04 6.4329784e-03 8.6474995e-04 5.7681976e-04
  2.2099228e-03 1.0007902e-02 2.4433355e-04 9.4470775e-01 1.6234360e-06]] index_of_max:8
output:[[6.7477096e-03 2.0449408e-03 5.0433147e-01 2.1711987e-02 2.7243090e-01
  9.4762599e-06 1.8795305e-01 7.4876544e-07 4.7624307e-03 7.3564729e-06]] index_of_max:2
output:[[5.22879509e-06 8.83535467e-09 1.91603942e-08 5.76953516e-06
  2.94285144e-07 1.09930575e-01 5.44046600e-07 8.44313145e-01
  1.72280222e-02 2.85165142e-02]] index_of_max:7
output:[[5.1315993e-01 3.3559173e-03 2.1247651e-02 7.2420172e-02 9.1842760e-04
  8.7975522e-08 3.8630870e-01 3.6168745e-11 2.5889918e-03 2.1049003e-08]] index_of_max:0
output:[[9.5492798e-01 3.3864093e-05 1.3866162e-04 1.2052676e-02 1.5875694e-08
  3.7448526e-21 3.2843202e-02 1.6990941e-36 3.4758673e-06 4.4162191e-21]] index_of_max:0
output:[[6.9755077e-02 2.7401697e-02 2.0343797e-02 7.3669463e-01 6.6482507e-02
  7.7717414e-06 6.9197997e-02 2.4990026e-08 1.0116417e-02 8.7524352e-

output:[[2.1306634e-02 1.2975368e-02 1.3644567e-01 1.6780257e-01 4.9412191e-01
  2.6218462e-04 1.5381812e-01 2.0605362e-06 1.3246725e-02 1.8760456e-05]] index_of_max:4
output:[[5.02954982e-03 1.43354125e-02 1.59307872e-03 9.47109103e-01
  2.64783613e-02 3.03902459e-09 3.95820010e-03 1.64318865e-15
  1.49622641e-03 1.32417330e-14]] index_of_max:3
output:[[2.7633209e-03 1.5394100e-04 6.3033367e-04 3.1455730e-03 3.2768762e-03
  3.6017537e-01 1.6485837e-03 5.0486654e-01 7.5592376e-02 4.7747064e-02]] index_of_max:7
output:[[9.0351282e-03 1.7508343e-02 1.9084500e-03 9.4477254e-01 1.8901154e-02
  3.1457545e-09 6.5312944e-03 1.2154558e-15 1.3430063e-03 3.8708769e-14]] index_of_max:3
output:[[8.4094679e-01 3.1650929e-05 1.5858877e-03 9.2676776e-03 6.4797666e-07
  4.6928738e-16 1.4812919e-01 4.0033270e-22 3.8181002e-05 9.7364902e-16]] index_of_max:0
output:[[4.2232676e-07 1.3841381e-08 1.1034899e-14 3.4970025e-08 2.7939140e-12
  5.2621994e-02 1.3015349e-09 4.2770210e-01 4.4288859e-03 5.1524651e-

output:[[3.4915249e-08 6.4320353e-08 1.6496015e-18 2.5987530e-11 1.5695654e-16
  8.8854223e-02 2.0100378e-12 9.0948008e-02 7.2291255e-04 8.1947482e-01]] index_of_max:9
output:[[3.2341450e-05 3.1804683e-07 7.5819582e-07 4.3405445e-05 1.2344258e-05
  2.0267907e-01 5.4716697e-06 7.2585571e-01 2.8383391e-02 4.2987194e-02]] index_of_max:7
output:[[4.2243010e-01 1.7510952e-03 4.5712907e-03 2.3454538e-02 8.7550165e-05
  6.3313792e-08 5.4735899e-01 3.8120195e-11 3.4627254e-04 1.2276291e-08]] index_of_max:6
output:[[4.8287795e-03 4.7016038e-06 2.0519327e-04 6.4032152e-05 1.0495424e-05
  1.6560973e-04 2.8472184e-04 1.1469028e-05 9.9442494e-01 1.2614901e-08]] index_of_max:8
output:[[2.0151919e-02 4.7059223e-01 2.9556881e-04 4.8303968e-01 1.3746354e-02
  4.7116182e-04 1.1510746e-02 1.6870874e-11 1.8717123e-04 5.1924271e-06]] index_of_max:3
output:[[1.0482729e-01 3.5365727e-02 4.8347592e-02 5.2956897e-01 1.2844291e-01
  2.0832452e-04 1.2983717e-01 4.0725868e-06 2.3396911e-02 9.8428757e-07]] index_o

output:[[7.1397886e-02 1.9373954e-03 2.1088280e-02 3.6461768e-03 6.3136038e-03
  5.4359725e-03 3.4883372e-02 3.1034739e-04 8.5495758e-01 2.9386249e-05]] index_of_max:8
output:[[8.0777006e-03 1.8261863e-03 2.2260062e-01 1.9572021e-02 3.8893008e-01
  4.5411048e-06 3.5223776e-01 2.1597022e-09 6.7505520e-03 5.5157511e-07]] index_of_max:4
output:[[1.2815595e-01 8.0029508e-03 8.0041036e-02 1.8967703e-02 4.1970570e-02
  2.7290462e-02 1.1656610e-01 3.4904948e-03 5.7513064e-01 3.8410956e-04]] index_of_max:8
output:[[3.5765622e-06 3.2873521e-07 1.4929088e-12 4.1905520e-07 2.2545994e-10
  9.3585104e-02 3.1353490e-08 4.6330020e-01 8.6033735e-03 4.3450692e-01]] index_of_max:7
output:[[0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  1.0000000e+00 0.0000000e+00 1.6490669e-23 2.8404033e-21 1.4093319e-32]] index_of_max:5
output:[[1.0959503e-03 2.6445357e-05 9.4398507e-05 1.3884823e-03 6.5935170e-04
  2.8740734e-01 4.7749162e-04 5.8948994e-01 6.5207198e-02 5.4153427e-02]] index_o

output:[[5.7070847e-27 2.0283842e-33 4.7186074e-30 8.7811636e-27 5.2121149e-30
  1.0000000e+00 7.4020578e-31 2.7334549e-10 9.5579197e-11 2.4563194e-12]] index_of_max:5
output:[[1.3159769e-02 2.1493898e-03 2.4558289e-01 5.6925949e-02 4.1782349e-01
  8.1506281e-05 2.4523674e-01 5.6262803e-07 1.9033181e-02 6.4526635e-06]] index_of_max:4
output:[[5.2856341e-02 1.5636683e-02 1.7388400e-01 1.3237815e-01 3.3988318e-01
  4.7859794e-04 2.5447527e-01 2.5981033e-05 3.0240029e-02 1.4175344e-04]] index_of_max:4
output:[[5.3895813e-29 0.0000000e+00 2.4724111e-29 1.4419386e-25 5.1615024e-30
  1.0000000e+00 9.6948891e-30 2.8532625e-09 3.1150556e-20 9.0311908e-10]] index_of_max:5
output:[[1.1012357e-02 3.9900057e-03 6.4016524e-04 9.7629422e-01 2.4798620e-03
  2.4025327e-11 5.3695366e-03 7.4469151e-16 2.1391052e-04 4.4142558e-16]] index_of_max:3
output:[[1.3337316e-03 5.0553220e-04 2.9409444e-03 1.3262519e-03 5.6917872e-03
  6.0607255e-01 7.6231232e-04 3.2270467e-01 4.1144088e-02 1.7518258e-02]] index_o

...

output:[[7.6739900e-02 3.8353290e-02 2.1182501e-01 1.4873761e-01 1.7383094e-01
  4.5538447e-03 3.0662447e-01 1.2652663e-05 3.9115615e-02 2.0668826e-04]] index_of_max:6
output:[[4.6851240e-02 4.2478358e-03 2.9084027e-01 1.7142856e-02 1.3372980e-01
  1.4402828e-04 4.4271722e-01 3.3911036e-09 6.4325698e-02 9.1577624e-07]] index_of_max:6
output:[[0.02905543 0.00299948 0.01516272 0.01187129 0.02116206 0.43500307
  0.03554776 0.33263278 0.07598466 0.04058075]] index_of_max:5
output:[[4.2647056e-02 1.1213082e-02 2.5348270e-01 3.5872739e-02 3.1323013e-01
  5.5950845e-06 3.0682272e-01 4.6374987e-11 3.6725942e-02 1.3565022e-08]] index_of_max:4
output:[[0.0662745  0.00713841 0.05448965 0.0300776  0.07160788 0.27661708
  0.13050811 0.23044752 0.09594457 0.03689475]] index_of_max:5
output:[[0.0863829  0.0129551  0.09110507 0.04427414 0.1163799  0.18407959
  0.21444307 0.14342721 0.08085275 0.02610021]] index_of_max:6
output:[[0.08375797 0.03014227 0.15595898 0.1132393  0.23231159 0.03108464
  0.306

output:[[2.3831483e-02 1.9132777e-03 4.0078661e-01 9.1891391e-03 1.1999200e-01
  1.3630879e-05 4.2451587e-01 1.4916650e-11 1.9757586e-02 2.8614892e-07]] index_of_max:6
output:[[1.2580262e-01 4.8761610e-02 1.1469220e-01 6.6892594e-02 3.0101556e-01
  6.7011900e-03 2.2232613e-01 8.3419574e-05 1.1366779e-01 5.6883408e-05]] index_of_max:4
output:[[2.9234620e-02 2.2116469e-03 3.7144583e-01 9.9740615e-03 1.0197270e-01
  2.5926105e-05 4.5269653e-01 7.3354205e-11 3.2438245e-02 3.3860903e-07]] index_of_max:6
output:[[7.9507433e-02 1.5101045e-02 2.5000507e-01 5.4236189e-02 2.2837019e-01
  6.7819669e-03 3.1830207e-01 7.6210170e-05 4.6437636e-02 1.1821941e-03]] index_of_max:6
output:[[7.0076168e-02 4.6861477e-02 1.6815712e-01 1.8016030e-01 2.4517204e-01
  2.0012003e-03 2.5967979e-01 2.6734133e-06 2.7845535e-02 4.3746866e-05]] index_of_max:6
output:[[5.5580806e-02 2.9142139e-02 2.7110738e-01 1.4922322e-01 1.6806246e-01
  2.2245514e-04 2.8759941e-01 2.0518685e-07 3.9060391e-02 1.5404329e-06]] index_o

output:[[1.71125263e-01 6.79303054e-03 2.18147516e-01 4.34273556e-02
  4.56084684e-02 1.87370810e-04 4.55019414e-01 3.23657730e-07
  5.95730916e-02 1.18187716e-04]] index_of_max:6
output:[[0.12189264 0.01808429 0.1170862  0.06061161 0.11780251 0.22663122
  0.21496774 0.01915133 0.08966361 0.01410886]] index_of_max:5
output:[[8.38494524e-02 3.62181701e-02 2.14443266e-01 1.14118226e-01
  1.81955561e-01 6.00574445e-03 3.29233646e-01 1.65470756e-05
  3.34716812e-02 6.87633117e-04]] index_of_max:6
output:[[0.07788975 0.01140068 0.07540681 0.04293006 0.11072953 0.20976096
  0.18707283 0.17094685 0.08315668 0.03070581]] index_of_max:5
output:[[1.5401095e-02 3.3820650e-04 1.1418859e-02 1.4054385e-03 3.9477628e-03
  7.0672894e-01 1.1488267e-02 1.9917174e-01 2.6222322e-02 2.3877444e-02]] index_of_max:5
output:[[0.08099641 0.01580094 0.08969247 0.05660259 0.14860839 0.1506379
  0.23640318 0.12452088 0.07128373 0.02545356]] index_of_max:6
output:[[0.09246961 0.02614434 0.15647744 0.10415467 0.2081

output:[[0.11455604 0.03712382 0.11642542 0.1588678  0.13973258 0.08989368
  0.27502012 0.00217926 0.05550565 0.01069566]] index_of_max:6
output:[[3.5568401e-02 4.5851278e-03 3.0594394e-01 2.0506326e-02 2.1110611e-01
  2.1925861e-04 4.0142155e-01 8.9802947e-09 2.0639855e-02 9.4175493e-06]] index_of_max:6
output:[[0.12120901 0.00914378 0.23462659 0.02830079 0.03721301 0.00771387
  0.33906573 0.00106997 0.22012056 0.00153667]] index_of_max:6
output:[[5.7397146e-02 6.6134180e-03 2.6944572e-01 2.5931722e-02 1.4404979e-01
  1.4407940e-04 3.9446485e-01 1.1627492e-08 1.0195295e-01 4.0449916e-07]] index_of_max:6
output:[[0.11878283 0.01974984 0.11211243 0.05067691 0.15052068 0.08184547
  0.2781386  0.06370979 0.11389007 0.0105734 ]] index_of_max:6
output:[[0.05646647 0.00387949 0.04955376 0.01335487 0.04246224 0.45447743
  0.08049204 0.20870611 0.06014497 0.03046261]] index_of_max:5
output:[[2.0443654e-02 1.6642385e-03 4.2982477e-01 9.2420541e-03 1.3430612e-01
  8.5287329e-06 3.9101383e-01 4.3

output:[[1.3010493e-03 4.1327784e-03 3.3796491e-04 2.0822182e-02 2.1785523e-03
  3.8405007e-01 2.2690333e-03 4.1482773e-01 3.9915852e-02 1.3016482e-01]] index_of_max:7
output:[[4.9032358e-04 2.4450182e-03 9.6760275e-05 1.3610257e-02 6.9274358e-04
  3.7010685e-01 7.6205027e-04 4.3001330e-01 3.3596374e-02 1.4818633e-01]] index_of_max:7
output:[[0.07350075 0.00956717 0.06357352 0.02784785 0.079465   0.30846044
  0.13310531 0.20511931 0.07001349 0.02934721]] index_of_max:5
output:[[0.05467172 0.02144466 0.05089587 0.07600684 0.05342634 0.20796935
  0.1499219  0.18357158 0.15355538 0.04853632]] index_of_max:5
output:[[0.01653009 0.00321136 0.00886489 0.01220262 0.01391721 0.5174774
  0.02154838 0.3023152  0.05437474 0.04955813]] index_of_max:5
output:[[1.8900871e-01 8.4428340e-03 1.6271436e-01 4.6904959e-02 2.2454420e-02
  2.9173604e-04 5.0630611e-01 2.5824772e-06 6.3676409e-02 1.9782194e-04]] index_of_max:6
output:[[0.00713016 0.0011761  0.00277612 0.00453192 0.00341067 0.56177264
  0.0064